## Imports

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import folium
from folium.plugins import MarkerCluster

import ipywidgets as widgets
from ipywidgets import interact

## Arrets

In [2]:
data_arrets = pd.read_json('../data/arrets.json')

# transform coordinates
data_arrets["coordonnees_lon"] = data_arrets["coordonnees"].apply(lambda x : x['lon'] if x is not None else None)
data_arrets["coordonnees_lat"] = data_arrets["coordonnees"].apply(lambda x : x['lat'] if x is not None else None)
data_arrets.drop(columns='coordonnees', inplace=True)

# replace actif by boolean
data_arrets.actif = data_arrets.actif.map({"Y":True, "N":False})

# fill na
data_arrets.fillna(value=np.nan, inplace=True)

# filter only active stops
data_arrets_actif = data_arrets[data_arrets.actif == True]

### Cartographie des arrêts

In [3]:
def draw_map_tpg(coordonnees_centre, zoom_start=12):
    m = folium.Map(location=coordonnees_centre, zoom_start=zoom_start, min_zoom=9, control_scale=True)
    marker_cluster = MarkerCluster(name='Arrêts TPG').add_to(m)

    for i in range(len(data_arrets_actif)):
        lon = data_arrets_actif.iloc[i]['coordonnees_lon']
        lat = data_arrets_actif.iloc[i]['coordonnees_lat']

        if not np.isnan(lon) and not np.isnan(lat):
            popup_html = "<b>Nom :</b> {}<br>".format(data_arrets_actif.iloc[i]['nomarret'])
            popup_html += "<b>Commune :</b> {}<br>".format(data_arrets_actif.iloc[i]['commune'])
            popup_html += "<b>Pays :</b> {}<br>".format(data_arrets_actif.iloc[i]['pays'])
            popup_html += "<b>Code Arret :</b> {}<br>".format(data_arrets_actif.iloc[i]['arretcodelong'])

            if data_arrets_actif.iloc[i]['pays'] == 'CH':
                marker_color = 'red'
            else:
                marker_color = 'blue'

            folium.Marker(
                location=[lat, lon],
                tooltip=data_arrets_actif.iloc[i]['nomarret'],
                icon=folium.Icon(color=marker_color, icon="bus", prefix="fa"),
                popup=folium.Popup(popup_html, max_width=300)
            ).add_to(marker_cluster)

    return m


In [4]:
coordonnees_centre = [data_arrets_actif.coordonnees_lat.mean(), data_arrets_actif.coordonnees_lon.mean()]
m = draw_map_tpg(coordonnees_centre)
m

## Montees par arret

In [5]:
data_montees = pd.read_parquet('../data/montees-par-arret-par-ligne.parquet')

# transform date
data_montees['date'] = pd.to_datetime(data_montees['date'])

In [6]:
# Set default start and end dates
default_start_date = data_montees['date'].min()
default_end_date = data_montees['date'].max()

# Create date range picker widgets with default values
@interact(start_date=widgets.DatePicker(value=default_start_date), end_date=widgets.DatePicker(value=default_end_date))
def update_chart(start_date, end_date):
    start_date = pd.to_datetime(start_date)
    end_date = pd.to_datetime(end_date)
    filtered_data = data_montees[(data_montees['date'] >= start_date) &
                                 (data_montees['date'] <= end_date)]
    total_montees_par_arret_filtered = filtered_data.groupby(by='arret_code_long')[['nb_de_montees', 'nb_de_descentes']].sum().sort_values(by='nb_de_montees', ascending=False)
    total_montees_par_arret_filtered.reset_index(inplace=True)
    total_montees_par_arret_filtered = total_montees_par_arret_filtered.merge(right=data_arrets, how='left', left_on='arret_code_long', right_on='arretcodelong')

    fig = px.bar(total_montees_par_arret_filtered, x="nomarret", y="nb_de_montees",
                 hover_data=["arret_code_long"],
                 width=1200, height=600, orientation='v',
                 title='Total Montees par Arret',
                 #labels={'arret_code_long': 'Arret Code Long', 'nomarret':'Nom arrêt', 'nb_de_montees': 'Total Montees'}
                )
    fig.show()


interactive(children=(DatePicker(value=Timestamp('2021-03-01 00:00:00'), description='start_date', step=1), Da…

In [7]:
# Define a function to update the chart (heatmap)
def update_chart(start_date, end_date):
    start_date = pd.to_datetime(start_date)
    end_date = pd.to_datetime(end_date)
    filtered_data = data_montees[(data_montees['date'] >= start_date) &
                                 (data_montees['date'] <= end_date)]
    total_montees_par_arret_filtered = filtered_data.groupby(by='arret_code_long')[['nb_de_montees']].sum().sort_values(by='nb_de_montees', ascending=False)
    total_montees_par_arret_filtered.reset_index(inplace=True)
    total_montees_par_arret_filtered = total_montees_par_arret_filtered.merge(right=data_arrets, how='left', left_on='arret_code_long', right_on='arretcodelong')

    fig = px.density_mapbox(total_montees_par_arret_filtered,
                            lat='coordonnees_lat',
                            lon='coordonnees_lon',
                            z='nb_de_montees',
                            hover_name='arret_code_long',
                            hover_data=['nomarret'],
                            radius=20,
                            center=dict(lat=46.2044, lon=6.1432),
                            zoom=11,
                            mapbox_style="open-street-map",
                            width=900, height=600,
                            title=f"Total Montees par Arret (Heatmap) (du {start_date.strftime('%d/%m/%Y')} au {end_date.strftime('%d/%m/%Y')})",
                            labels={'nb_de_montees': 'Total Montees', 'nomarret': 'Arrêt'})
    fig.show()

# Set default start and end dates
default_start_date = data_montees['date'].min()
default_end_date = data_montees['date'].max()

# Create date range picker widgets with default values
@interact(start_date=widgets.DatePicker(value=default_start_date), end_date=widgets.DatePicker(value=default_end_date))
def draw_map_and_heatmap(start_date, end_date):
    start_date = pd.to_datetime(start_date)
    end_date = pd.to_datetime(end_date)
    data_arrets_actif = data_arrets[data_arrets.actif == True]


    # Update the heatmap
    update_chart(start_date, end_date)


interactive(children=(DatePicker(value=Timestamp('2021-03-01 00:00:00'), description='start_date', step=1), Da…